## [Click this link to see maps rendered!](https://nbviewer.jupyter.org/github/bimewok/geospatial_exercise/blob/82be261f39ef25e6a89778d89a45879d425e22a2/interactive_results.ipynb)

In [6]:
import folium
import pandas as pd
import geopandas as gpd
import numpy as np
import os
import branca
pd.set_option("display.max_rows", 20)



## Task One: Determining number of solar panels and Jul - Jan GHI difference for MA zip codes



In [7]:
data = pd.read_csv('https://raw.githubusercontent.com/bimewok/geospatial_exercise/main/outputs/zip_stats.csv', index_col=0)


display(data)

zip_code  num_solar_panels  jul_jan_ghi_diff
0        1001             146.0        178.200264
1        1002             397.0        177.233295
2        1003              23.0        178.953629
3        1005              10.0        177.658722
4        1007             231.0        176.342252
..        ...               ...               ...
515      2779              24.0        177.218206
516      2780             110.0        175.599726
517      2790             598.0        179.460933
518      2791              14.0        179.285100
519     12125               0.0        181.046238

[520 rows x 3 columns]

## Task Two: Find areas where January GHI is above the MA average

In [8]:
import pandas as pd


data = gpd.read_file('https://raw.githubusercontent.com/bimewok/geospatial_exercise/main/outputs/high_jan_ghi.geojson') 
data['idx'] = np.arange(len(data))
data['GHI'] = [round(i, 1) for i in data['ghi']]
min_ghi = np.min(data['GHI'])
max_ghi = np.max(data['GHI'])
                     
colorscale = branca.colormap.linear.YlOrRd_09.scale(min_ghi, max_ghi)
ghi_series = data.set_index("idx")["GHI"]


def style_function(feature):
    ghi = ghi_series.get(int(feature["id"][-5:]), None)
    return {
        "fillOpacity": 0.9,
        "weight": 0,
        "fillColor": "#black" if ghi is None else colorscale(ghi),
    }


m = folium.Map([42.4, -71], zoom_start=8, tiles='Stamen Toner')
h = folium.GeoJson(data,
              style_function=style_function).add_to(m)
h.add_child(
    folium.features.GeoJsonTooltip(['GHI'], labels=False)
)

m 

## Task Three: Make a surface model from lidar data

In [9]:

import os
import folium

m = folium.Map([42.3782, -71.06309], zoom_start=14, tiles="OpenStreetMap")

img = folium.raster_layers.ImageOverlay(
    name="Mercator projection SW",
    image='https://github.com/bimewok/geospatial_exercise/blob/main/intermediate_data/hillshade.jpg?raw=true',
    bounds=[[42.369275, -71.080845], [42.390549, -71.047266]],
    opacity=1,
    interactive=True,
    cross_origin=False,
    zindex=1,
)

folium.Popup("I am an image").add_to(img)

img.add_to(m)
folium.LayerControl().add_to(m)
m


## Task Four: Use surface model to extract heights of buildings

In [10]:
import pandas as pd
import branca

data = gpd.read_file('https://github.com/bimewok/geospatial_exercise/raw/main/outputs/charlestown_buildings_heights.geojson') 

data['idx'] = np.arange(len(data))
data['height '] = [round(i, 1) for i in data['height']]
min_ghi = np.min(data['height '])
max_ghi = np.max(data['height '])

colorscale = branca.colormap.linear.YlGnBu_09.scale(min_ghi, max_ghi-40)
height_series = data.set_index("idx")["height "]


def style_function(feature):
    heights = height_series.get(int(feature["id"][-5:]), None)
    return {
        "fillOpacity": 0.9,
        "weight": 0,
        "fillColor": "#black" if heights is None else colorscale(heights),
    }


m = folium.Map([42.3782, -71.06309], zoom_start=14, tiles="OpenStreetMap")
h = folium.GeoJson(data,
              style_function=style_function).add_to(m)
h.add_child(
    folium.features.GeoJsonTooltip(['height '], labels=True)
)

m 